In [2]:
import pandas as pd
import geopandas as gpd
import numpy as np
import gurobipy as gp
from gurobipy import GRB
import networkx as nx
import itertools
import sys
sys.path.append('..')
from security_game.target import Target
from security_game.green_security_game import GreenSecurityGame
from security_game.infra_security_game import InfraSecurityGame

from solvers.mip import mip
from solvers.nash import nash
from solvers.double_oracle import double_oracle
from solvers.double_oracle_sf import double_oracle_sf
from solvers.no_regret import regret_matching
from solvers.simple_sse_lp import solve_sse_lp
from solvers.nfg_sse_lp import solve_general_sum_normal_form

from utils.random_utils import generate_random_utility_matrix_like, generate_random_target_utility_matrix_like, generate_random_target_utility_matrix_like_v2

import time
from matplotlib import pyplot as plt
from collections import defaultdict, Counter
import copy

In [3]:
seeds = [1,2,3,4,5,6,7,8,9,10]

# GSG

In [4]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

## DO NFG Random Target Values (done)

In [26]:
schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)

supports=[]
defender_actions_sizes = []
attacker_actions_sizes = []
iterations_to_converge = []
iteration_times_li = []
gaps_li = []
num_defenders_li = []

for num_defenders in [1,2]:
    for seed in seeds:
        np.random.seed(seed)
        print(f"starting seed: {seed}")
        gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
        gsg.generate(num_attackers=1, 
                 num_defenders=num_defenders, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post) for i in range(num_defenders)],
                 num_timesteps=8, 
                 generate_utility_matrix=False,
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=False, 
                 general_sum=False, 
                 **schedule_form_kwargs)

        D_a, D_d, u, A_a, A_d, c, iteration_times, gaps = double_oracle(gsg,eps=1e-12, verbose=False) #How to randomize for NFG DO?
        support = sum([1 for p in D_d if p!=0])
        supports.append(support)
        iterations_to_converge.append(c)
        defender_actions_sizes.append(len(A_d))
        attacker_actions_sizes.append(len(A_a))
        iteration_times_li.append(iteration_times)
        gaps_li.append(gaps)
        num_defenders_li.append(num_defenders)

starting seed: 1
starting seed: 2
starting seed: 3
starting seed: 4
starting seed: 5
starting seed: 6
starting seed: 7
starting seed: 8
starting seed: 9
starting seed: 10
starting seed: 1
starting seed: 2
starting seed: 3
starting seed: 4
starting seed: 5
starting seed: 6
starting seed: 7
starting seed: 8
starting seed: 9
starting seed: 10


In [29]:
df = pd.DataFrame()
seedli = seeds + seeds
df["seed"] = seedli
df["num_timesteps"] = [8 for i in range(len(seedli))]
df["num_defenders"] = num_defenders_li
df["num_attackers"] = [1 for i in range(len(seedli))]
df["num_clusters"] = [10 for i in range(len(seedli))]
df["dims"] = [7 for i in range(len(seedli))]
df["defense_time_threshold"] = [1 for i in range(len(seedli))]
df["force_return"] = [False for i in range(len(seedli))]
df["iterations_to_converge"] = iterations_to_converge
df["defender_actions_size"] = defender_actions_sizes
df["attacker_actions_size"] = attacker_actions_sizes
df["iteration_time"] = iteration_times_li
df["gap"] = gaps_li
df["def_support"] = supports


# Step 2: Explode list columns
exploded_df = df.explode(["iteration_time", "gap"], ignore_index=True)

# Optional: Add a column for iteration number within each grouped trial
exploded_df["iteration_number"] = exploded_df.groupby(
    ["seed","num_defenders"]
).cumcount()

# Reorder if desired
cols = [
    "seed", "num_timesteps","num_attackers", "num_defenders", "num_clusters", "dims", "force_return", "defense_time_threshold",
    "iteration_number", "iteration_time", "gap", 
    "iterations_to_converge", "def_support", "defender_actions_size", "attacker_actions_size"
]
exploded_df = exploded_df[cols]

# Make iteration number 1-indexed
exploded_df["iteration_number"] += 1
exploded_df

seed  num_timesteps  num_attackers  num_defenders  num_clusters  dims  \
0       1              8              1              1            10     7   
1       1              8              1              1            10     7   
2       1              8              1              1            10     7   
3       1              8              1              1            10     7   
4       1              8              1              1            10     7   
..    ...            ...            ...            ...           ...   ...   
288    10              8              1              2            10     7   
289    10              8              1              2            10     7   
290    10              8              1              2            10     7   
291    10              8              1              2            10     7   
292    10              8              1              2            10     7   

     force_return  defense_time_threshold  iteration_number iteration_time  \
0           False                       1                 1       0.018625   
1           False                       1                 2        0.01808   
2           False                       1                 3       0.021733   
3           False                       1                 4        0.01217   
4           False                       1                 5       0.023556   
..            ...                     ...               ...            ...   
288         False                       1                18        0.16648   
289         False                       1                19       0.183922   
290         False                       1                20       0.133645   
291         False                       1                21       0.148406   
292         False                       1                22       0.203583   

          gap  iterations_to_converge  def_support  defender_actions_size  \
0    0.748019                      11            4                      8   
1    0.748019                      11            4                      8   
2    0.578936                      11            4                      8   
3    0.578936                      11            4                      8   
4    0.184155                      11            4                      8   
..        ...                     ...          ...                    ...   
288  0.057745                      22            7                     21   
289  0.078932                      22            7                     21   
290  0.048876                      22            7                     21   
291  0.064428                      22            7                     21   
292       0.0                      22            7                     21   

     attacker_actions_size  
0                        6  
1                        6  
2                        6  
3                        6  
4                        6  
..                     ...  
288                      7  
289                      7  
290                      7  
291                      7  
292                      7  

[293 rows x 15 columns]

In [30]:
exploded_df.to_csv("GSG_NFG_DO_RANDOM_TARGET_VALUES_FR_FALSE.csv")

## RM Algos w/ Matrix from random target values

### RM (done)

In [19]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=1, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.utility_matrix, runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=False, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21723831433169066
Iteration 10 gap:  0.14765174788643387
Iteration 15 gap:  0.1314924131369276
Iteration 20 gap:  0.1435998288772009
Iteration 25 gap:  0.12814458742604062
Iteration 30 gap:  0.1718830760932452
Iteration 35 gap:  0.16831852444284062
Iteration 40 gap:  0.16956568288001417
Iteration 45 gap:  0.13604157333659822
Iteration 50 gap:  0.09908805556236855
Iteration 55 gap:  0.07813052646761287
Iteration 60 gap:  0.08332852474281444
Iteration 65 gap:  0.07646435928419515
Iteration 70 gap:  0.05947192522284883
Iteration 75 gap:  0.05231808026048684
Iteration 80 gap:  0.047424855799586885
Iteration 85 gap:  0.05648477198658325
Iteration 90 gap:  0.058452964853945744
Iteration 95 gap:  0.06096410254131007
Iteration 100 gap:  0.07723093188378699
Iteration 105 gap:  0.09702496515689274
Iteration 110 gap:  0.11276424676903507
Iteration 115 gap:  0.12304712278316787
Iteration 120 gap:  0.11589526099401376
Iteration 125 g

In [22]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              1   
1        1              8              1              1   
2        1              8              1              1   
3        1              8              1              1   
4        1              8              1              1   
...    ...            ...            ...            ...   
5698    10              8              1              1   
5699    10              8              1              1   
5700    10              8              1              1   
5701    10              8              1              1   
5702    10              8              1              1   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1          True                0        0.157047   
1                          1          True                1        0.162086   
2                          1          True                2        0.158237   
3                          1          True                3        0.157952   
4                          1          True                4        0.154361   
...                      ...           ...              ...             ...   
5698                       1          True              526        0.195775   
5699                       1          True              527        0.177078   
5700                       1          True              528        0.199475   
5701                       1          True              529        0.178296   
5702                       1          True              530        0.200807   

          gaps  
0     0.217238  
1     0.147652  
2     0.131492  
3       0.1436  
4     0.128145  
...        ...  
5698  0.025191  
5699  0.024932  
5700  0.024586  
5701   0.02416  
5702  0.023656  

[5703 rows x 9 columns]

In [24]:
exploded_df.to_csv("GSG_NFG_RM_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### RM+

In [38]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=1, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.utility_matrix, runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=True, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.09701716361205281
Iteration 10 gap:  0.16620788881977794
Iteration 15 gap:  0.09217560795160157
Iteration 20 gap:  0.08981371418717876
Iteration 25 gap:  0.08770603573270819
Iteration 30 gap:  0.09304471229975453
Iteration 35 gap:  0.0760975624451577
Iteration 40 gap:  0.09746563433856015
Iteration 45 gap:  0.09419015984422019
Iteration 50 gap:  0.08163126357064521
Iteration 55 gap:  0.09158927092615077
Iteration 60 gap:  0.08705076800382089
Iteration 65 gap:  0.07379470911438624
Iteration 70 gap:  0.07542773281669396
Iteration 75 gap:  0.08003904381851878


KeyboardInterrupt: 

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_NFG_RMP_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### PRM+

In [39]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=1, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.utility_matrix, runtime=120, interval=5, iterations=10000, averaging=2, alternations=True, plus=True, predictive=True, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.28093741988591686
Iteration 10 gap:  0.10000197038903874
Iteration 15 gap:  0.11728873809408075
Iteration 20 gap:  0.1252580499793361
Iteration 25 gap:  0.12686085210197362
Iteration 30 gap:  0.11394375814375324
Iteration 35 gap:  0.10758817952768007
Iteration 40 gap:  0.10868328540355354


KeyboardInterrupt: 

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_NFG_PRMP_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### RM random matrix

In [5]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
gsg.generate(num_attackers=1, 
             num_defenders=1, 
             home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
             num_timesteps=8, 
             generate_utility_matrix=True, 
             random_target_values=False,
             defense_time_threshold=1, 
             generate_actions=False, 
             force_return=False, 
             general_sum=False, 
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(gsg.utility_matrix), high=np.max(gsg.utility_matrix), size=gsg.utility_matrix.shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=False, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21357899845142872
Iteration 10 gap:  0.19012841144430467
Iteration 15 gap:  0.21511366974417145
Iteration 20 gap:  0.1805036949716791
Iteration 25 gap:  0.13982591238566208
Iteration 30 gap:  0.1245890944981696
Iteration 35 gap:  0.11484862714701069
Iteration 40 gap:  0.10668194660064398
Iteration 45 gap:  0.11820086663704937
Iteration 50 gap:  0.12222499614503107
Iteration 55 gap:  0.11510728862686209
Iteration 60 gap:  0.10056263563599394
Iteration 65 gap:  0.08532959891027092
Iteration 70 gap:  0.08284783342992472
Iteration 75 gap:  0.07619259181838
Iteration 80 gap:  0.07314384394135923
Iteration 85 gap:  0.07101363300438618
Iteration 90 gap:  0.07443872785373534
Iteration 95 gap:  0.07953075979527824
Iteration 100 gap:  0.08315913090243751
Iteration 105 gap:  0.08460448684697344
Iteration 110 gap:  0.08376708336802871
Iteration 115 gap:  0.07818024140506843
Iteration 120 gap:  0.06714250096364499
Iteration 125 gap: 

In [6]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [False for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              1   
1        1              8              1              1   
2        1              8              1              1   
3        1              8              1              1   
4        1              8              1              1   
...    ...            ...            ...            ...   
4567    10              8              1              1   
4568    10              8              1              1   
4569    10              8              1              1   
4570    10              8              1              1   
4571    10              8              1              1   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1         False                1        0.211219   
1                          1         False                2        0.192022   
2                          1         False                3        0.234425   
3                          1         False                4        0.236415   
4                          1         False                5        0.213243   
...                      ...           ...              ...             ...   
4567                       1         False              467        0.264632   
4568                       1         False              468        0.197909   
4569                       1         False              469        0.197282   
4570                       1         False              470        0.217786   
4571                       1         False              471         0.18498   

          gaps  iteration_number  
0     0.213579                 5  
1     0.190128                10  
2     0.215114                15  
3     0.180504                20  
4     0.139826                25  
...        ...               ...  
4567  0.009432              2335  
4568  0.009388              2340  
4569  0.009321              2345  
4570  0.009229              2350  
4571  0.009109              2355  

[4572 rows x 10 columns]

In [7]:
exploded_df.to_csv("GSG_NFG_RM_RANDOM_MATRIX_FR_FALSE.csv")

### RM+ random matrix

In [9]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
gsg.generate(num_attackers=1, 
             num_defenders=1, 
             home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
             num_timesteps=8, 
             generate_utility_matrix=True, 
             random_target_values=False,
             defense_time_threshold=1, 
             generate_actions=False, 
             force_return=False, 
             general_sum=False, 
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(gsg.utility_matrix), high=np.max(gsg.utility_matrix), size=gsg.utility_matrix.shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=1, alternations=True, plus=True, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.19481141199805305
Iteration 10 gap:  0.17318736546585084
Iteration 15 gap:  0.15004677829346685
Iteration 20 gap:  0.1453291771587839
Iteration 25 gap:  0.13283390727175454
Iteration 30 gap:  0.12165893730394628
Iteration 35 gap:  0.10734204039175427
Iteration 40 gap:  0.0968858928314143
Iteration 45 gap:  0.08975437515132836
Iteration 50 gap:  0.0876723922092564
Iteration 55 gap:  0.082471067621253
Iteration 60 gap:  0.07781148822842318
Iteration 65 gap:  0.0726359649236179
Iteration 70 gap:  0.06761867326472426
Iteration 75 gap:  0.06240568490903459
Iteration 80 gap:  0.05888699951425869
Iteration 85 gap:  0.0564864995566596
Iteration 90 gap:  0.05668722238248222
Iteration 95 gap:  0.05546785429386197
Iteration 100 gap:  0.054708426886682315
Iteration 105 gap:  0.05213708130551403
Iteration 110 gap:  0.04861255223198532
Iteration 115 gap:  0.04521488477719979
Iteration 120 gap:  0.04444404354040746
Iteration 125 gap:  

In [10]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              1   
1        1              8              1              1   
2        1              8              1              1   
3        1              8              1              1   
4        1              8              1              1   
...    ...            ...            ...            ...   
4845    10              8              1              1   
4846    10              8              1              1   
4847    10              8              1              1   
4848    10              8              1              1   
4849    10              8              1              1   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1          True                1         0.22258   
1                          1          True                2        0.186894   
2                          1          True                3        0.264658   
3                          1          True                4        0.214134   
4                          1          True                5        0.207722   
...                      ...           ...              ...             ...   
4845                       1          True              482        0.255591   
4846                       1          True              483        0.162101   
4847                       1          True              484         0.23645   
4848                       1          True              485        0.191768   
4849                       1          True              486        0.155814   

          gaps  iteration_number  
0     0.194811                 5  
1     0.173187                10  
2     0.150047                15  
3     0.145329                20  
4     0.132834                25  
...        ...               ...  
4845  0.002326              2410  
4846  0.002314              2415  
4847  0.002305              2420  
4848  0.002298              2425  
4849  0.002294              2430  

[4850 rows x 10 columns]

In [11]:
exploded_df.to_csv("GSG_NFG_RMP_NEW_RANDOM_MATRIX_FR_FALSE.csv")

### PRM+ random matrix

In [12]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
gsg.generate(num_attackers=1, 
             num_defenders=1, 
             home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
             num_timesteps=8, 
             generate_utility_matrix=True, 
             random_target_values=False,
             defense_time_threshold=1, 
             generate_actions=False, 
             force_return=False, 
             general_sum=False, 
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(gsg.utility_matrix), high=np.max(gsg.utility_matrix), size=gsg.utility_matrix.shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=2, alternations=True, plus=True, predictive=True, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21040124226995258
Iteration 10 gap:  0.1510200776880774
Iteration 15 gap:  0.12526073285605213
Iteration 20 gap:  0.12102372962727093
Iteration 25 gap:  0.10886347934332624
Iteration 30 gap:  0.10292739876575563
Iteration 35 gap:  0.09655966846068001
Iteration 40 gap:  0.09067287067708113
Iteration 45 gap:  0.08203967955042232
Iteration 50 gap:  0.07538952371978783
Iteration 55 gap:  0.06859319881923803
Iteration 60 gap:  0.06113137887508685
Iteration 65 gap:  0.05466470302858084
Iteration 70 gap:  0.050066744807901215
Iteration 75 gap:  0.04612463609030373
Iteration 80 gap:  0.04616186860005986
Iteration 85 gap:  0.04468233610702077
Iteration 90 gap:  0.043346316294638504
Iteration 95 gap:  0.04058096040049575
Iteration 100 gap:  0.03784084037761615
Iteration 105 gap:  0.0370369174297277
Iteration 110 gap:  0.03672001511092676
Iteration 115 gap:  0.03543978902282999
Iteration 120 gap:  0.03418749074409849
Iteration 125 

In [13]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [False for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              1   
1        1              8              1              1   
2        1              8              1              1   
3        1              8              1              1   
4        1              8              1              1   
...    ...            ...            ...            ...   
4750    10              8              1              1   
4751    10              8              1              1   
4752    10              8              1              1   
4753    10              8              1              1   
4754    10              8              1              1   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1         False                1        0.257167   
1                          1         False                2        0.207754   
2                          1         False                3        0.223814   
3                          1         False                4        0.240326   
4                          1         False                5        0.201669   
...                      ...           ...              ...             ...   
4750                       1         False              506        0.205202   
4751                       1         False              507        0.173706   
4752                       1         False              508        0.158408   
4753                       1         False              509        0.205331   
4754                       1         False              510         0.25322   

          gaps  iteration_number  
0     0.210401                 5  
1      0.15102                10  
2     0.125261                15  
3     0.121024                20  
4     0.108863                25  
...        ...               ...  
4750  0.000421              2530  
4751  0.000417              2535  
4752  0.000414              2540  
4753  0.000411              2545  
4754  0.000408              2550  

[4755 rows x 10 columns]

In [14]:
exploded_df.to_csv("GSG_NFG_PRMP_RANDOM_MATRIX.csv")

### GSG SF DO Random target values (done)

In [5]:
schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_animal_value":  2350, 
    "defender_animal_value": 22966, 
    "defender_step_cost": 0, 
}

df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)

supports=[]
iterations_to_converge = []
defender_actions_sizes = []
attacker_actions_sizes = []
iteration_times_li = []
gaps_li = []

gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7, escape_line_points=None)
gsg.generate(num_attackers=1, 
             num_defenders=2, 
             home_base_assignments=[(kabo_djembe, bomassa, inner_post),(kabo_djembe, bomassa, inner_post)], 
             num_timesteps=8, 
             generate_utility_matrix=False, 
             defense_time_threshold=1, 
             force_return=True, 
             **schedule_form_kwargs,
             **general_sum_kwargs)
for seed in seeds:
    print(f"starting seed: {seed}")
    np.random.seed(seed)
    sdict_copy = copy.deepcopy(gsg.schedule_form_dict)
    sdict_copy["target_utilities"] = generate_random_target_utility_matrix_like_v2(gsg.schedule_form_dict["target_utilities"], general_sum=False, respect_sign_roles=True)
    print(sdict_copy["target_utilities"])
    # print(gsg.schedule_form_dict)
    # print(sdict_copy)
    # print("starting double oracle sf")
    # print(sdict_copy["target_utilities"])
    D_a, D_d, u, A_a, A_d, c, iteration_times, gaps = double_oracle_sf(sdict_copy,eps=1e-12, verbose=False)
    # print("Done")
    support = sum([1 for p in D_d if p!=0])
    supports.append(support)
    iterations_to_converge.append(c)
    defender_actions_sizes.append(len(A_d))
    attacker_actions_sizes.append(len(A_a))
    iteration_times_li.append(iteration_times)
    gaps_li.append(gaps)

starting seed: 1
[[-0.43869008 -0.7297122  -0.23115595 -0.8822086  -0.17539625 -0.68152874
  -0.4368638  -0.57350304 -0.41701584 -0.55429701]
 [-0.4365905  -0.69578556 -0.03367697 -0.32575078 -0.06003472 -0.12280555
  -0.21357455 -0.36752792 -0.16924108 -0.22501836]
 [ 0.4365905   0.69578556  0.03367697  0.32575078  0.06003472  0.12280555
   0.21357455  0.36752792  0.16924108  0.22501836]
 [ 0.43869008  0.7297122   0.23115595  0.8822086   0.17539625  0.68152874
   0.4368638   0.57350304  0.41701584  0.55429701]]
Set parameter WLSAccessID
Set parameter WLSSecret
Set parameter LicenseID to value 2455389
Academic license 2455389 - for non-commercial use only - registered to jc___@columbia.edu
starting seed: 2
[[-0.63385102 -0.54494711 -0.5647787  -0.52990557 -0.43982399 -0.79254068
  -0.85887682 -0.63205068 -0.85171187 -0.29143727]
 [-0.45492654 -0.05862241 -0.16362901 -0.45427661 -0.21181531 -0.35281309
  -0.23134574 -0.5112135  -0.32316277 -0.1105385 ]
 [ 0.45492654  0.05862241  0.16362

### old target value randomization

In [5]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "num_clusters": [10 for i in range(len(seeds))],
    "dims": [7 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "def_support": supports,
    "iterations_to_converge": iterations_to_converge,
    "iteration_time": iteration_times_li,
    "gap": gaps_li,
    "defender_actions_size": defender_actions_sizes,
    "attacker_actions_size": attacker_actions_sizes
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_time", "gap"], ignore_index=True)

# Optional: Add a column for iteration number within each grouped trial
exploded_df["iteration_number"] = exploded_df.groupby(
    ["seed"]
).cumcount()

# Reorder if desired
cols = ["seed",
    "num_timesteps", "num_defenders", "num_clusters", "dims", "defense_time_threshold",
    "iteration_number", "iteration_time", "gap", 
    "iterations_to_converge", "def_support", "defender_actions_size", "attacker_actions_size"
]
exploded_df = exploded_df[cols]

# Make iteration number 1-indexed
exploded_df["iteration_number"] += 1

exploded_df

seed  num_timesteps  num_defenders  num_clusters  dims  \
0       1              8              2            10     7   
1       1              8              2            10     7   
2       1              8              2            10     7   
3       1              8              2            10     7   
4       1              8              2            10     7   
..    ...            ...            ...           ...   ...   
104    10              8              2            10     7   
105    10              8              2            10     7   
106    10              8              2            10     7   
107    10              8              2            10     7   
108    10              8              2            10     7   

     defense_time_threshold  iteration_number iteration_time       gap  \
0                         1                 1       0.011556  0.445618   
1                         1                 2       0.002012  0.556458   
2                         1                 3       0.002149  0.293122   
3                         1                 4       0.003221  0.033927   
4                         1                 5       0.002006  0.031977   
..                      ...               ...            ...       ...   
104                       1                 6       0.005134  0.452924   
105                       1                 7       0.003043  0.028749   
106                       1                 8       0.004182  0.028235   
107                       1                 9       0.003045  0.615872   
108                       1                10       0.004128       0.0   

     iterations_to_converge  def_support  defender_actions_size  \
0                         6            1                      4   
1                         6            1                      4   
2                         6            1                      4   
3                         6            1                      4   
4                         6            1                      4   
..                      ...          ...                    ...   
104                      10            5                      5   
105                      10            5                      5   
106                      10            5                      5   
107                      10            5                      5   
108                      10            5                      5   

     attacker_actions_size  
0                        3  
1                        3  
2                        3  
3                        3  
4                        3  
..                     ...  
104                      7  
105                      7  
106                      7  
107                      7  
108                      7  

[109 rows x 13 columns]

In [6]:
exploded_df.to_csv("GSG_SF_DO_RANDOM_TARGET_VALUES.csv")

### new target value randomization

In [6]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "num_clusters": [10 for i in range(len(seeds))],
    "dims": [7 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "def_support": supports,
    "iterations_to_converge": iterations_to_converge,
    "iteration_time": iteration_times_li,
    "gap": gaps_li,
    "defender_actions_size": defender_actions_sizes,
    "attacker_actions_size": attacker_actions_sizes
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_time", "gap"], ignore_index=True)

# Optional: Add a column for iteration number within each grouped trial
exploded_df["iteration_number"] = exploded_df.groupby(
    ["seed"]
).cumcount()

# Reorder if desired
cols = ["seed",
    "num_timesteps", "num_defenders", "num_clusters", "dims", "defense_time_threshold",
    "iteration_number", "iteration_time", "gap", 
    "iterations_to_converge", "def_support", "defender_actions_size", "attacker_actions_size"
]
exploded_df = exploded_df[cols]

# Make iteration number 1-indexed
exploded_df["iteration_number"] += 1

exploded_df

seed  num_timesteps  num_defenders  num_clusters  dims  \
0       1              8              2            10     7   
1       1              8              2            10     7   
2       1              8              2            10     7   
3       1              8              2            10     7   
4       1              8              2            10     7   
..    ...            ...            ...           ...   ...   
104    10              8              2            10     7   
105    10              8              2            10     7   
106    10              8              2            10     7   
107    10              8              2            10     7   
108    10              8              2            10     7   

     defense_time_threshold  iteration_number iteration_time       gap  \
0                         1                 1       0.005626  0.445618   
1                         1                 2       0.002259  0.556458   
2                         1                 3       0.003269  0.293122   
3                         1                 4       0.002113  0.033927   
4                         1                 5        0.00332  0.031977   
..                      ...               ...            ...       ...   
104                       1                 6       0.002462  0.452924   
105                       1                 7       0.004184  0.028749   
106                       1                 8       0.003632  0.028235   
107                       1                 9       0.003033  0.615872   
108                       1                10       0.005061       0.0   

     iterations_to_converge  def_support  defender_actions_size  \
0                         6            1                      4   
1                         6            1                      4   
2                         6            1                      4   
3                         6            1                      4   
4                         6            1                      4   
..                      ...          ...                    ...   
104                      10            5                      5   
105                      10            5                      5   
106                      10            5                      5   
107                      10            5                      5   
108                      10            5                      5   

     attacker_actions_size  
0                        3  
1                        3  
2                        3  
3                        3  
4                        3  
..                     ...  
104                      7  
105                      7  
106                      7  
107                      7  
108                      7  

[109 rows x 13 columns]

### RM

In [ ]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=2, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.schedule_form_dict["defender_utility_matrix"], runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=False, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21723831433169066
Iteration 10 gap:  0.14765174788643387
Iteration 15 gap:  0.1314924131369276
Iteration 20 gap:  0.1435998288772009
Iteration 25 gap:  0.12814458742604062
Iteration 30 gap:  0.1718830760932452
Iteration 35 gap:  0.16831852444284062
Iteration 40 gap:  0.16956568288001417
Iteration 45 gap:  0.13604157333659822
Iteration 50 gap:  0.09908805556236855
Iteration 55 gap:  0.07813052646761287
Iteration 60 gap:  0.08332852474281444
Iteration 65 gap:  0.07646435928419515
Iteration 70 gap:  0.05947192522284883
Iteration 75 gap:  0.05231808026048684
Iteration 80 gap:  0.047424855799586885
Iteration 85 gap:  0.05648477198658325
Iteration 90 gap:  0.058452964853945744
Iteration 95 gap:  0.06096410254131007
Iteration 100 gap:  0.07723093188378699
Iteration 105 gap:  0.09702496515689274
Iteration 110 gap:  0.11276424676903507
Iteration 115 gap:  0.12304712278316787
Iteration 120 gap:  0.11589526099401376
Iteration 125 g

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_SF_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### RM+

In [ ]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=2, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.schedule_form_dict["defender_utility_matrix"], runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=True, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21723831433169066
Iteration 10 gap:  0.14765174788643387
Iteration 15 gap:  0.1314924131369276
Iteration 20 gap:  0.1435998288772009
Iteration 25 gap:  0.12814458742604062
Iteration 30 gap:  0.1718830760932452
Iteration 35 gap:  0.16831852444284062
Iteration 40 gap:  0.16956568288001417
Iteration 45 gap:  0.13604157333659822
Iteration 50 gap:  0.09908805556236855
Iteration 55 gap:  0.07813052646761287
Iteration 60 gap:  0.08332852474281444
Iteration 65 gap:  0.07646435928419515
Iteration 70 gap:  0.05947192522284883
Iteration 75 gap:  0.05231808026048684
Iteration 80 gap:  0.047424855799586885
Iteration 85 gap:  0.05648477198658325
Iteration 90 gap:  0.058452964853945744
Iteration 95 gap:  0.06096410254131007
Iteration 100 gap:  0.07723093188378699
Iteration 105 gap:  0.09702496515689274
Iteration 110 gap:  0.11276424676903507
Iteration 115 gap:  0.12304712278316787
Iteration 120 gap:  0.11589526099401376
Iteration 125 g

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_SF_RMP_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### PRM+

In [ ]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=2, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.schedule_form_dict["defender_utility_matrix"], runtime=120, interval=5, iterations=10000, averaging=2, alternations=True, plus=True, predictive=True, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21723831433169066
Iteration 10 gap:  0.14765174788643387
Iteration 15 gap:  0.1314924131369276
Iteration 20 gap:  0.1435998288772009
Iteration 25 gap:  0.12814458742604062
Iteration 30 gap:  0.1718830760932452
Iteration 35 gap:  0.16831852444284062
Iteration 40 gap:  0.16956568288001417
Iteration 45 gap:  0.13604157333659822
Iteration 50 gap:  0.09908805556236855
Iteration 55 gap:  0.07813052646761287
Iteration 60 gap:  0.08332852474281444
Iteration 65 gap:  0.07646435928419515
Iteration 70 gap:  0.05947192522284883
Iteration 75 gap:  0.05231808026048684
Iteration 80 gap:  0.047424855799586885
Iteration 85 gap:  0.05648477198658325
Iteration 90 gap:  0.058452964853945744
Iteration 95 gap:  0.06096410254131007
Iteration 100 gap:  0.07723093188378699
Iteration 105 gap:  0.09702496515689274
Iteration 110 gap:  0.11276424676903507
Iteration 115 gap:  0.12304712278316787
Iteration 120 gap:  0.11589526099401376
Iteration 125 g

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_SF_PRMP_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### RM random matrix

In [6]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []

gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
gsg.generate(num_attackers=1, 
             num_defenders=2, 
             home_base_assignments=[(kabo_djembe, bomassa, inner_post),(kabo_djembe, bomassa, inner_post)], 
             num_timesteps=8, 
             generate_utility_matrix=True, 
             random_target_values=False,
             defense_time_threshold=1, 
             generate_actions=False, 
             force_return=True, 
             general_sum=False, 
             **schedule_form_kwargs)

for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(gsg.schedule_form_dict["defender_utility_matrix"]), high=np.max(gsg.schedule_form_dict["defender_utility_matrix"]), size=gsg.schedule_form_dict["defender_utility_matrix"].shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=False, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.2216491458551029
Iteration 10 gap:  0.16941863371873297
Iteration 15 gap:  0.1617844801289746
Iteration 20 gap:  0.1470333745993695
Iteration 25 gap:  0.13505882676250092
Iteration 30 gap:  0.10681506794627371
Iteration 35 gap:  0.09325111822499477
Iteration 40 gap:  0.0908168793180742
Iteration 45 gap:  0.08690943918205202
Iteration 50 gap:  0.08765740106310888
Iteration 55 gap:  0.08804811443718277
Iteration 60 gap:  0.08371096128693184
Iteration 65 gap:  0.08378504513814283
Iteration 70 gap:  0.07854434769936713
Iteration 75 gap:  0.06844198684837088
Iteration 80 gap:  0.06810253111980619
Iteration 85 gap:  0.06873176117733176
Iteration 90 gap:  0.06120506096907402
Iteration 95 gap:  0.06298577964572205
Iteration 100 gap:  0.06038099665299096
Iteration 105 gap:  0.05361266990672925
Iteration 110 gap:  0.05238087552996218
Iteration 115 gap:  0.0484098396854129
Iteration 120 gap:  0.04432673070893034
Iteration 125 gap: 

In [7]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0         1              8              1              2   
1         1              8              1              2   
2         1              8              1              2   
3         1              8              1              2   
4         1              8              1              2   
...     ...            ...            ...            ...   
19806    10              8              1              2   
19807    10              8              1              2   
19808    10              8              1              2   
19809    10              8              1              2   
19810    10              8              1              2   

       defense_time_threshold  force_return  interval_number iteration_times  \
0                           1          True                1        0.048102   
1                           1          True                2        0.063649   
2                           1          True                3        0.060958   
3                           1          True                4        0.052997   
4                           1          True                5        0.055588   
...                       ...           ...              ...             ...   
19806                       1          True             1975        0.048114   
19807                       1          True             1976        0.047825   
19808                       1          True             1977        0.039729   
19809                       1          True             1978        0.042384   
19810                       1          True             1979        0.046955   

           gaps  iteration_number  
0      0.221649                 5  
1      0.169419                10  
2      0.161784                15  
3      0.147033                20  
4      0.135059                25  
...         ...               ...  
19806  0.002841              9875  
19807  0.002766              9880  
19808  0.002684              9885  
19809  0.002596              9890  
19810  0.002502              9895  

[19811 rows x 10 columns]

In [8]:
exploded_df.to_csv("GSG_SF_RM_RANDOM_MATRIX.csv")

### RM+ random matrix

In [9]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []

gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
gsg.generate(num_attackers=1, 
             num_defenders=2, 
             home_base_assignments=[(kabo_djembe, bomassa, inner_post),(kabo_djembe, bomassa, inner_post)], 
             num_timesteps=8, 
             generate_utility_matrix=True, 
             random_target_values=False,
             defense_time_threshold=1, 
             generate_actions=False, 
             force_return=True, 
             general_sum=False, 
             **schedule_form_kwargs)

for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(gsg.schedule_form_dict["defender_utility_matrix"]), high=np.max(gsg.schedule_form_dict["defender_utility_matrix"]), size=gsg.schedule_form_dict["defender_utility_matrix"].shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=1, alternations=True, plus=True, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.17155036660575929
Iteration 10 gap:  0.14802389376007025
Iteration 15 gap:  0.13949414744123273
Iteration 20 gap:  0.11819128607625484
Iteration 25 gap:  0.09954383344513795
Iteration 30 gap:  0.08246296315884794
Iteration 35 gap:  0.07338174085123383
Iteration 40 gap:  0.07293444329199367
Iteration 45 gap:  0.07552734910082548
Iteration 50 gap:  0.07909382944996757
Iteration 55 gap:  0.07295084727149376
Iteration 60 gap:  0.061398805862430905
Iteration 65 gap:  0.0557154676797722
Iteration 70 gap:  0.05724073455127998
Iteration 75 gap:  0.05251282791938694
Iteration 80 gap:  0.04601301596245627
Iteration 85 gap:  0.045632033887922974
Iteration 90 gap:  0.0465311096135641
Iteration 95 gap:  0.0455693454415983
Iteration 100 gap:  0.04255441954109501
Iteration 105 gap:  0.03886867216670897
Iteration 110 gap:  0.035109498504185765
Iteration 115 gap:  0.032515244970131196
Iteration 120 gap:  0.03021944850783026
Iteration 125

In [10]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0         1              8              1              2   
1         1              8              1              2   
2         1              8              1              2   
3         1              8              1              2   
4         1              8              1              2   
...     ...            ...            ...            ...   
19985    10              8              1              2   
19986    10              8              1              2   
19987    10              8              1              2   
19988    10              8              1              2   
19989    10              8              1              2   

       defense_time_threshold  force_return  interval_number iteration_times  \
0                           1          True                1         0.04728   
1                           1          True                2        0.047577   
2                           1          True                3        0.047771   
3                           1          True                4        0.047304   
4                           1          True                5        0.052653   
...                       ...           ...              ...             ...   
19985                       1          True             1995        0.047419   
19986                       1          True             1996        0.047488   
19987                       1          True             1997        0.063702   
19988                       1          True             1998        0.053582   
19989                       1          True             1999        0.047908   

           gaps  iteration_number  
0       0.17155                 5  
1      0.148024                10  
2      0.139494                15  
3      0.118191                20  
4      0.099544                25  
...         ...               ...  
19985   0.00003              9975  
19986   0.00003              9980  
19987   0.00003              9985  
19988  0.000032              9990  
19989  0.000036              9995  

[19990 rows x 10 columns]

In [11]:
exploded_df.to_csv("GSG_SF_RMP_NEW_RANDOM_MATRIX.csv")

### PRM+ random matrix

In [12]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []

gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
gsg.generate(num_attackers=1, 
             num_defenders=2, 
             home_base_assignments=[(kabo_djembe, bomassa, inner_post),(kabo_djembe, bomassa, inner_post)], 
             num_timesteps=8, 
             generate_utility_matrix=True, 
             random_target_values=False,
             defense_time_threshold=1, 
             generate_actions=False, 
             force_return=True, 
             general_sum=False, 
             **schedule_form_kwargs)

for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(gsg.schedule_form_dict["defender_utility_matrix"]), high=np.max(gsg.schedule_form_dict["defender_utility_matrix"]), size=gsg.schedule_form_dict["defender_utility_matrix"].shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=2, alternations=True, plus=True, predictive=True, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.17066640315137058
Iteration 10 gap:  0.1327255242572951
Iteration 15 gap:  0.10744373079610281
Iteration 20 gap:  0.09705003060757306
Iteration 25 gap:  0.08212600148617427
Iteration 30 gap:  0.0744457199556936
Iteration 35 gap:  0.06972177770296367
Iteration 40 gap:  0.0672361681594888
Iteration 45 gap:  0.06184822472680451
Iteration 50 gap:  0.056869072224249584
Iteration 55 gap:  0.05241753258307186
Iteration 60 gap:  0.048142668711693426
Iteration 65 gap:  0.04401507628933149
Iteration 70 gap:  0.041315829722095576
Iteration 75 gap:  0.03806692004221035
Iteration 80 gap:  0.03688334528352538
Iteration 85 gap:  0.03526241426903204
Iteration 90 gap:  0.03319519552703554
Iteration 95 gap:  0.031550366505196326
Iteration 100 gap:  0.02874261778679421
Iteration 105 gap:  0.026262161820720498
Iteration 110 gap:  0.02331509493627837
Iteration 115 gap:  0.02073975501749248
Iteration 120 gap:  0.018578100755096805
Iteration 1

In [13]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0         1              8              1              2   
1         1              8              1              2   
2         1              8              1              2   
3         1              8              1              2   
4         1              8              1              2   
...     ...            ...            ...            ...   
15176    10              8              1              2   
15177    10              8              1              2   
15178    10              8              1              2   
15179    10              8              1              2   
15180    10              8              1              2   

       defense_time_threshold  force_return  interval_number iteration_times  \
0                           1          True                1          0.0633   
1                           1          True                2        0.047613   
2                           1          True                3        0.047867   
3                           1          True                4        0.049343   
4                           1          True                5        0.042892   
...                       ...           ...              ...             ...   
15176                       1          True             1391        0.047548   
15177                       1          True             1392        0.047355   
15178                       1          True             1393         0.06279   
15179                       1          True             1394        0.047169   
15180                       1          True             1395        0.047204   

           gaps  iteration_number  
0      0.170666                 5  
1      0.132726                10  
2      0.107444                15  
3       0.09705                20  
4      0.082126                25  
...         ...               ...  
15176   0.00001              6955  
15177   0.00001              6960  
15178   0.00001              6965  
15179   0.00001              6970  
15180   0.00001              6975  

[15181 rows x 10 columns]

In [14]:
exploded_df.to_csv("GSG_SF_PRMP_RANDOM_MATRIX.csv")

# ISG

In [4]:
gdf = gpd.read_file("chinatown_infra.geojson")

# Step 1: Handle relevant columns
infra_columns = [
    "id", "name", "power", "man_made", "amenity",
    "generator:method", "generator:source", "geometry"
]
available_columns = [col for col in infra_columns if col in gdf.columns]
gdf = gdf[available_columns].copy()

# Step 2: Extract generator type if present
gdf["generator_type"] = gdf.get("generator:method")
if "generator_type" not in gdf.columns or gdf["generator_type"].isnull().all():
    gdf["generator_type"] = gdf.get("generator:source")

# Step 3: Construct unified 'type' column
gdf["type"] = gdf.get("power")
if "amenity" in gdf.columns:
    gdf["type"] = gdf["type"].combine_first(gdf["amenity"])
if "man_made" in gdf.columns:
    gdf["type"] = gdf["type"].combine_first(gdf["man_made"])

# Step 4: Refine generator classification (solar vs. other)
gdf.loc[(gdf["type"] == "generator") & (gdf["generator_type"] == "photovoltaic"), "type"] = "solar_generator"
gdf.loc[(gdf["type"] == "generator") & (gdf["generator_type"] == "solar"), "type"] = "solar_generator"

# Step 5: Drop raw columns now that 'type' is finalized
df_simple = gdf[["id", "name", "type", "geometry"]].copy()

# Step 6: Separate nodes and ways
df_nodes = df_simple[df_simple["id"].str.contains("node")].copy()
df_nodes["x"] = df_nodes.geometry.x
df_nodes["y"] = df_nodes.geometry.y
df_nodes = df_nodes.drop(columns=["geometry"])

df_ways = df_simple[df_simple["id"].str.contains("way")].copy()
df_ways = df_ways.set_geometry("geometry").to_crs("EPSG:32618")
df_ways["centroid"] = df_ways.geometry.centroid
df_ways = df_ways.set_geometry("centroid").to_crs("EPSG:4326")
df_ways["x"] = df_ways.geometry.x
df_ways["y"] = df_ways.geometry.y
df_ways = df_ways.drop(columns=["geometry", "centroid"])

# Step 7: Combine nodes and ways
df_combined = pd.concat([df_nodes, df_ways], ignore_index=True)
df_combined = pd.concat([df_nodes, df_ways], ignore_index=True)
ny_blocks_gdf =  gpd.read_file("tl_2020_36_tabblock20.shp")
INFRA_WEIGHTS = {
    # Power Infrastructure
    "plant": 1.5,
    "generator": 1.35,
    "solar_generator": 0.95,
    "substation": 1.45,
    "transformer": 1.25,
    "tower": 1.1,
    "pole": 0.85,
    "line": 1.0,
    "minor_line": 0.9,
    "cable": 0.95,
    "switchgear": 1.2,
    "busbar": 0.8,
    "bay": 0.85,
    "converter": 1.05,
    "insulator": 0.75,
    "portal": 0.75,
    "connection": 0.7,
    "compensator": 1.0,
    "rectifier": 0.95,
    "inverter": 0.95,
    "storage": 0.9,

    # Healthcare
    "hospital": 1.5,
    "clinic": 1.35,

    # Education
    "school": 1.25,
    "university": 1.4,

    # Water & Sanitation
    "water_works": 1.45,
    "wastewater_plant": 1.4,

    # Government & Emergency Services
    "fire_station": 1.3,
    "police": 1.4,
    "courthouse": 1.2,

    # Critical Infrastructure
    "bunker_silo": 1.0,

    # Communications
    "communications_tower": 1.25,
}


## DO NFG Random Target Values (done)

In [12]:
import warnings
warnings.filterwarnings('ignore', category=FutureWarning)

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 3,
    "defender_penalty_factor": 3,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

# Bounding box for Hoboken, NJ
# bbox_hoboken_small = (40.752635, 40.745600, -74.030386,-74.043903)
bbox_hoboken_low = (40.745411, 40.735486, -74.025857,-74.041479)
bbox_hoboken_east = (40.748337, 40.734641,-74.022961,-74.031286)
bbox_downtown = (40.718721, 40.714078, -73.996074, -74.002651)
bbox_downtown_large = (40.7215, 40.710, -73.9935, -74.010)
# 40.7060, -74.0140, 40.7205, -73.9935
college_police = (40.743293077312465, -74.02670221027175)
police_station = (40.73768931976651, -74.02990519431108)
traffic_police = (40.7366602084371, -74.03449866349136)
downtown_station = (40.71232433042349, -74.00187755238431)
fifth_ave_station = (40.71637413934789, -73.9973285259067)
fifth_precinct = (40.71625547686622, -73.99736909131171)
booking_station = (40.716191530904815, -74.00102237385177)
police_plaza = (40.71236124409745, -74.00173715463521)
troop_nyc = (40.71657885026091, -74.00641139014367)
first_precinct = (40.720411300417446, -74.0070247584372)

num_timesteps_li = []
num_attackers_li = []
num_defenders_li = []
supports=[]
dims_li = []
dts = []
frs = []
defender_actions_sizes = []
attacker_actions_sizes = []
iterations_to_converge = []
iteration_times_li = []
gaps_li = []

for num_defenders in [1,2,3]:
    for seed in seeds:
        print(f"starting seed {seed}")
        isg = InfraSecurityGame(df_combined, ny_blocks_gdf, INFRA_WEIGHTS, bbox=bbox_downtown_large)
        isg.generate(num_attackers=1,
                     num_defenders=num_defenders,
                     home_base_assignments=[(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza) for i in range(num_defenders)],
                     num_timesteps=8,
                     generate_utility_matrix=False,
                     random_target_values=True,
                     generate_actions=False,
                     force_return=True,
                     defense_time_threshold=1,
                     **general_sum_kwargs,
                     **schedule_form_kwargs)
        D_a, D_d, u, A_a, A_d, c, iteration_times, gaps = double_oracle(isg,eps=1e-12, verbose=False)
        support = sum([1 for p in D_d if p!=0])
        supports.append(support)
        num_defenders_li.append(num_defenders)
        iterations_to_converge.append(c)
        defender_actions_sizes.append(len(A_d))
        attacker_actions_sizes.append(len(A_a))
        iteration_times_li.append(iteration_times)
        gaps_li.append(gaps)

starting seed 1
starting seed 2
starting seed 3
starting seed 4
starting seed 5
starting seed 6
starting seed 7
starting seed 8
starting seed 9
starting seed 10
starting seed 1
starting seed 2
starting seed 3
starting seed 4
starting seed 5
starting seed 6
starting seed 7
starting seed 8
starting seed 9
starting seed 10
starting seed 1
starting seed 2
starting seed 3
starting seed 4
starting seed 5
starting seed 6
starting seed 7
starting seed 8
starting seed 9
starting seed 10


In [13]:
df = pd.DataFrame()
seedli = seeds + seeds + seeds
df["seed"] = seedli
df["num_timesteps"] = [8 for i in range(len(seedli))]
df["num_defenders"] = num_defenders_li
df["num_attackers"] = [1 for i in range(len(seedli))]
df["defense_time_threshold"] = [1 for i in range(len(seedli))]
df["force_return"] = [True for i in range(len(seedli))]
df["iterations_to_converge"] = iterations_to_converge
df["defender_actions_size"] = defender_actions_sizes
df["attacker_actions_size"] = attacker_actions_sizes
df["iteration_time"] = iteration_times_li
df["gap"] = gaps_li
df["def_support"] = supports


# Step 2: Explode list columns
exploded_df = df.explode(["iteration_time", "gap"], ignore_index=True)

# Optional: Add a column for iteration number within each grouped trial
exploded_df["iteration_number"] = exploded_df.groupby(
    ["seed","num_defenders"]
).cumcount()

# Reorder if desired
cols = [
    "seed", "num_timesteps","num_attackers", "num_defenders", "force_return", "defense_time_threshold",
    "iteration_number", "iteration_time", "gap", 
    "iterations_to_converge", "def_support", "defender_actions_size", "attacker_actions_size"
]
exploded_df = exploded_df[cols]

# Make iteration number 1-indexed
exploded_df["iteration_number"] += 1
exploded_df

seed  num_timesteps  num_attackers  num_defenders  force_return  \
0       1              8              1              1          True   
1       1              8              1              1          True   
2       1              8              1              1          True   
3       1              8              1              1          True   
4       1              8              1              1          True   
..    ...            ...            ...            ...           ...   
530    10              8              1              3          True   
531    10              8              1              3          True   
532    10              8              1              3          True   
533    10              8              1              3          True   
534    10              8              1              3          True   

     defense_time_threshold  iteration_number iteration_time       gap  \
0                         1                 1       0.075685  0.974164   
1                         1                 2        0.06536  0.974164   
2                         1                 3       0.071107  0.452389   
3                         1                 4        0.05308  0.945846   
4                         1                 5       0.077032   0.26784   
..                      ...               ...            ...       ...   
530                       1                19        0.54278  0.296275   
531                       1                20       0.769799  0.141613   
532                       1                21       0.207611  0.510938   
533                       1                22       0.760782  0.126348   
534                       1                23        1.02627       0.0   

     iterations_to_converge  def_support  defender_actions_size  \
0                        11            6                     11   
1                        11            6                     11   
2                        11            6                     11   
3                        11            6                     11   
4                        11            6                     11   
..                      ...          ...                    ...   
530                      23            9                     23   
531                      23            9                     23   
532                      23            9                     23   
533                      23            9                     23   
534                      23            9                     23   

     attacker_actions_size  
0                        6  
1                        6  
2                        6  
3                        6  
4                        6  
..                     ...  
530                     10  
531                     10  
532                     10  
533                     10  
534                     10  

[535 rows x 13 columns]

In [14]:
exploded_df.to_csv("ISG_NFG_DO_RANDOM_TARGET_VALUES.csv")

## RM Algos w/ Matrix from random target values

### RM (done)

In [19]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=1, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.utility_matrix, runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=False, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21723831433169066
Iteration 10 gap:  0.14765174788643387
Iteration 15 gap:  0.1314924131369276
Iteration 20 gap:  0.1435998288772009
Iteration 25 gap:  0.12814458742604062
Iteration 30 gap:  0.1718830760932452
Iteration 35 gap:  0.16831852444284062
Iteration 40 gap:  0.16956568288001417
Iteration 45 gap:  0.13604157333659822
Iteration 50 gap:  0.09908805556236855
Iteration 55 gap:  0.07813052646761287
Iteration 60 gap:  0.08332852474281444
Iteration 65 gap:  0.07646435928419515
Iteration 70 gap:  0.05947192522284883
Iteration 75 gap:  0.05231808026048684
Iteration 80 gap:  0.047424855799586885
Iteration 85 gap:  0.05648477198658325
Iteration 90 gap:  0.058452964853945744
Iteration 95 gap:  0.06096410254131007
Iteration 100 gap:  0.07723093188378699
Iteration 105 gap:  0.09702496515689274
Iteration 110 gap:  0.11276424676903507
Iteration 115 gap:  0.12304712278316787
Iteration 120 gap:  0.11589526099401376
Iteration 125 g

In [22]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              1   
1        1              8              1              1   
2        1              8              1              1   
3        1              8              1              1   
4        1              8              1              1   
...    ...            ...            ...            ...   
5698    10              8              1              1   
5699    10              8              1              1   
5700    10              8              1              1   
5701    10              8              1              1   
5702    10              8              1              1   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1          True                0        0.157047   
1                          1          True                1        0.162086   
2                          1          True                2        0.158237   
3                          1          True                3        0.157952   
4                          1          True                4        0.154361   
...                      ...           ...              ...             ...   
5698                       1          True              526        0.195775   
5699                       1          True              527        0.177078   
5700                       1          True              528        0.199475   
5701                       1          True              529        0.178296   
5702                       1          True              530        0.200807   

          gaps  
0     0.217238  
1     0.147652  
2     0.131492  
3       0.1436  
4     0.128145  
...        ...  
5698  0.025191  
5699  0.024932  
5700  0.024586  
5701   0.02416  
5702  0.023656  

[5703 rows x 9 columns]

In [24]:
exploded_df.to_csv("GSG_NFG_RM_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### RM+

In [38]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=1, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.utility_matrix, runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=True, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.09701716361205281
Iteration 10 gap:  0.16620788881977794
Iteration 15 gap:  0.09217560795160157
Iteration 20 gap:  0.08981371418717876
Iteration 25 gap:  0.08770603573270819
Iteration 30 gap:  0.09304471229975453
Iteration 35 gap:  0.0760975624451577
Iteration 40 gap:  0.09746563433856015
Iteration 45 gap:  0.09419015984422019
Iteration 50 gap:  0.08163126357064521
Iteration 55 gap:  0.09158927092615077
Iteration 60 gap:  0.08705076800382089
Iteration 65 gap:  0.07379470911438624
Iteration 70 gap:  0.07542773281669396
Iteration 75 gap:  0.08003904381851878


KeyboardInterrupt: 

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_NFG_RMP_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### PRM+

In [39]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=1, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.utility_matrix, runtime=120, interval=5, iterations=10000, averaging=2, alternations=True, plus=True, predictive=True, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.28093741988591686
Iteration 10 gap:  0.10000197038903874
Iteration 15 gap:  0.11728873809408075
Iteration 20 gap:  0.1252580499793361
Iteration 25 gap:  0.12686085210197362
Iteration 30 gap:  0.11394375814375324
Iteration 35 gap:  0.10758817952768007
Iteration 40 gap:  0.10868328540355354


KeyboardInterrupt: 

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_NFG_PRMP_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### RM random matrix

In [16]:
# Bounding box for Hoboken, NJ
# bbox_hoboken_small = (40.752635, 40.745600, -74.030386,-74.043903)
bbox_hoboken_low = (40.745411, 40.735486, -74.025857,-74.041479)
bbox_hoboken_east = (40.748337, 40.734641,-74.022961,-74.031286)
bbox_downtown = (40.718721, 40.714078, -73.996074, -74.002651)
bbox_downtown_large = (40.7215, 40.710, -73.9935, -74.010)
# 40.7060, -74.0140, 40.7205, -73.9935
college_police = (40.743293077312465, -74.02670221027175)
police_station = (40.73768931976651, -74.02990519431108)
traffic_police = (40.7366602084371, -74.03449866349136)
downtown_station = (40.71232433042349, -74.00187755238431)
fifth_ave_station = (40.71637413934789, -73.9973285259067)
fifth_precinct = (40.71625547686622, -73.99736909131171)
booking_station = (40.716191530904815, -74.00102237385177)
police_plaza = (40.71236124409745, -74.00173715463521)
troop_nyc = (40.71657885026091, -74.00641139014367)
first_precinct = (40.720411300417446, -74.0070247584372)

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 3,
    "defender_penalty_factor": 3,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

isg = InfraSecurityGame(df_combined, ny_blocks_gdf, INFRA_WEIGHTS, bbox=bbox_downtown_large)
isg.generate(num_attackers=1,
             num_defenders=1,
             home_base_assignments=[(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza)],
             num_timesteps=8,
             generate_utility_matrix=True,
             generate_actions=False,
             force_return=False,
             defense_time_threshold=1,
             **general_sum_kwargs,
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(isg.utility_matrix), high=np.max(isg.utility_matrix), size=isg.utility_matrix.shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=False, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

C:\Users\Noah\GameGenerators\notebooks\..\security_game\infra_security_game.py:65: FutureWarning: The `north`, `south`, `east`, and `west` parameters are deprecated and will be removed in the v2.0.0 release. Use the `bbox` parameter instead. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  self.graph = ox.graph_from_bbox(north, south, east, west, network_type="drive")
C:\Users\Noah\GameGenerators\notebooks\..\security_game\infra_security_game.py:65: FutureWarning: The expected order of coordinates in `bbox` will change in the v2.0.0 release to `(left, bottom, right, top)`.
  self.graph = ox.graph_from_bbox(north, south, east, west, network_type="drive")


starting seed 1
game done generating, running
Iteration 5 gap:  0.1623888323134659
Iteration 10 gap:  0.1581314244222301
Iteration 15 gap:  0.12067240747091629
Iteration 20 gap:  0.10462656291379269
Iteration 25 gap:  0.09279667890880305
Iteration 30 gap:  0.09285254610622384
Iteration 35 gap:  0.08880736661428706
Iteration 40 gap:  0.07941032331044406
Iteration 45 gap:  0.07265168557631246
Iteration 50 gap:  0.06629419193102182
Iteration 55 gap:  0.0666795547025365
Iteration 60 gap:  0.06069884938075798
Iteration 65 gap:  0.054119083429724435
Iteration 70 gap:  0.05197468918379311
Iteration 75 gap:  0.055624984150103196
Iteration 80 gap:  0.05064623252195288
Iteration 85 gap:  0.04682717432635353
Iteration 90 gap:  0.04437942267501627
Iteration 95 gap:  0.04268939180146003
Iteration 100 gap:  0.042434859914205536
Iteration 105 gap:  0.044026810591676735
Iteration 110 gap:  0.04452047780634916
Iteration 115 gap:  0.04030046292261319
Iteration 120 gap:  0.039544160578265264
Iteration 12

In [17]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [False for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              1   
1        1              8              1              1   
2        1              8              1              1   
3        1              8              1              1   
4        1              8              1              1   
...    ...            ...            ...            ...   
1554    10              8              1              1   
1555    10              8              1              1   
1556    10              8              1              1   
1557    10              8              1              1   
1558    10              8              1              1   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1         False                1        0.653977   
1                          1         False                2        0.639594   
2                          1         False                3        0.653824   
3                          1         False                4        0.654857   
4                          1         False                5        0.629818   
...                      ...           ...              ...             ...   
1554                       1         False              152        0.633827   
1555                       1         False              153        0.650822   
1556                       1         False              154        0.649097   
1557                       1         False              155        0.636102   
1558                       1         False              156        0.635027   

          gaps  iteration_number  
0     0.162389                 5  
1     0.158131                10  
2     0.120672                15  
3     0.104627                20  
4     0.092797                25  
...        ...               ...  
1554  0.016336               760  
1555  0.016468               765  
1556  0.016329               770  
1557  0.016081               775  
1558  0.015709               780  

[1559 rows x 10 columns]

In [18]:
exploded_df.to_csv("ISG_NFG_RM_RANDOM_MATRIX.csv")

### RM+ random matrix

In [19]:
# Bounding box for Hoboken, NJ
# bbox_hoboken_small = (40.752635, 40.745600, -74.030386,-74.043903)
bbox_hoboken_low = (40.745411, 40.735486, -74.025857,-74.041479)
bbox_hoboken_east = (40.748337, 40.734641,-74.022961,-74.031286)
bbox_downtown = (40.718721, 40.714078, -73.996074, -74.002651)
bbox_downtown_large = (40.7215, 40.710, -73.9935, -74.010)
# 40.7060, -74.0140, 40.7205, -73.9935
college_police = (40.743293077312465, -74.02670221027175)
police_station = (40.73768931976651, -74.02990519431108)
traffic_police = (40.7366602084371, -74.03449866349136)
downtown_station = (40.71232433042349, -74.00187755238431)
fifth_ave_station = (40.71637413934789, -73.9973285259067)
fifth_precinct = (40.71625547686622, -73.99736909131171)
booking_station = (40.716191530904815, -74.00102237385177)
police_plaza = (40.71236124409745, -74.00173715463521)
troop_nyc = (40.71657885026091, -74.00641139014367)
first_precinct = (40.720411300417446, -74.0070247584372)

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 3,
    "defender_penalty_factor": 3,

}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

isg = InfraSecurityGame(df_combined, ny_blocks_gdf, INFRA_WEIGHTS, bbox=bbox_downtown_large)
isg.generate(num_attackers=1,
             num_defenders=1,
             home_base_assignments=[(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza)],
             num_timesteps=8,
             generate_utility_matrix=True,
             generate_actions=False,
             force_return=False,
             defense_time_threshold=1,
             **general_sum_kwargs,
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(isg.utility_matrix), high=np.max(isg.utility_matrix), size=isg.utility_matrix.shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=1, alternations=True, plus=True, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

C:\Users\Noah\GameGenerators\notebooks\..\security_game\infra_security_game.py:65: FutureWarning: The `north`, `south`, `east`, and `west` parameters are deprecated and will be removed in the v2.0.0 release. Use the `bbox` parameter instead. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  self.graph = ox.graph_from_bbox(north, south, east, west, network_type="drive")
C:\Users\Noah\GameGenerators\notebooks\..\security_game\infra_security_game.py:65: FutureWarning: The expected order of coordinates in `bbox` will change in the v2.0.0 release to `(left, bottom, right, top)`.
  self.graph = ox.graph_from_bbox(north, south, east, west, network_type="drive")


starting seed 1
game done generating, running
Iteration 5 gap:  0.14417436288849733
Iteration 10 gap:  0.13710255450500108
Iteration 15 gap:  0.12293856874891929
Iteration 20 gap:  0.09847562942544591
Iteration 25 gap:  0.07987564672100261
Iteration 30 gap:  0.07473331620571921
Iteration 35 gap:  0.06970543754993341
Iteration 40 gap:  0.06437415436093791
Iteration 45 gap:  0.056036816023290414
Iteration 50 gap:  0.04994789194398902
Iteration 55 gap:  0.0462363775859006
Iteration 60 gap:  0.04797649344240179
Iteration 65 gap:  0.04682592904770816
Iteration 70 gap:  0.04614719879946705
Iteration 75 gap:  0.04518077253604369
Iteration 80 gap:  0.04339175323730532
Iteration 85 gap:  0.04082368103462802
Iteration 90 gap:  0.037829798316591556
Iteration 95 gap:  0.03514617915264773
Iteration 100 gap:  0.03349990924188739
Iteration 105 gap:  0.03225343530643121
Iteration 110 gap:  0.03114300510555662
Iteration 115 gap:  0.030017591982623548
Iteration 120 gap:  0.028889271576243936
Iteration 1

In [20]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [False for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              1   
1        1              8              1              1   
2        1              8              1              1   
3        1              8              1              1   
4        1              8              1              1   
...    ...            ...            ...            ...   
1594    10              8              1              1   
1595    10              8              1              1   
1596    10              8              1              1   
1597    10              8              1              1   
1598    10              8              1              1   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1         False                1        0.636609   
1                          1         False                2        0.602695   
2                          1         False                3        0.618256   
3                          1         False                4        0.616706   
4                          1         False                5        0.630784   
...                      ...           ...              ...             ...   
1594                       1         False              156        0.618438   
1595                       1         False              157        0.615999   
1596                       1         False              158        0.618696   
1597                       1         False              159        0.618564   
1598                       1         False              160        0.617311   

          gaps  iteration_number  
0     0.144174                 5  
1     0.137103                10  
2     0.122939                15  
3     0.098476                20  
4     0.079876                25  
...        ...               ...  
1594   0.00738               780  
1595  0.007304               785  
1596  0.007189               790  
1597  0.007095               795  
1598  0.006978               800  

[1599 rows x 10 columns]

In [21]:
exploded_df.to_csv("ISG_NFG_RMP_NEW_RANDOM_MATRIX.csv")

### PRM+ random matrix

In [22]:
# Bounding box for Hoboken, NJ
# bbox_hoboken_small = (40.752635, 40.745600, -74.030386,-74.043903)
bbox_hoboken_low = (40.745411, 40.735486, -74.025857,-74.041479)
bbox_hoboken_east = (40.748337, 40.734641,-74.022961,-74.031286)
bbox_downtown = (40.718721, 40.714078, -73.996074, -74.002651)
bbox_downtown_large = (40.7215, 40.710, -73.9935, -74.010)
# 40.7060, -74.0140, 40.7205, -73.9935
college_police = (40.743293077312465, -74.02670221027175)
police_station = (40.73768931976651, -74.02990519431108)
traffic_police = (40.7366602084371, -74.03449866349136)
downtown_station = (40.71232433042349, -74.00187755238431)
fifth_ave_station = (40.71637413934789, -73.9973285259067)
fifth_precinct = (40.71625547686622, -73.99736909131171)
booking_station = (40.716191530904815, -74.00102237385177)
police_plaza = (40.71236124409745, -74.00173715463521)
troop_nyc = (40.71657885026091, -74.00641139014367)
first_precinct = (40.720411300417446, -74.0070247584372)

schedule_form_kwargs = {
    "schedule_form": False,
    "simple": False,
    "attacker_penalty_factor": 3,
    "defender_penalty_factor": 3,

}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

isg = InfraSecurityGame(df_combined, ny_blocks_gdf, INFRA_WEIGHTS, bbox=bbox_downtown_large)
isg.generate(num_attackers=1,
             num_defenders=1,
             home_base_assignments=[(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza)],
             num_timesteps=8,
             generate_utility_matrix=True,
             generate_actions=False,
             force_return=False,
             defense_time_threshold=1,
             **general_sum_kwargs,
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(isg.utility_matrix), high=np.max(isg.utility_matrix), size=isg.utility_matrix.shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=2, alternations=True, plus=True, predictive=True, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

C:\Users\Noah\GameGenerators\notebooks\..\security_game\infra_security_game.py:65: FutureWarning: The `north`, `south`, `east`, and `west` parameters are deprecated and will be removed in the v2.0.0 release. Use the `bbox` parameter instead. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  self.graph = ox.graph_from_bbox(north, south, east, west, network_type="drive")
C:\Users\Noah\GameGenerators\notebooks\..\security_game\infra_security_game.py:65: FutureWarning: The expected order of coordinates in `bbox` will change in the v2.0.0 release to `(left, bottom, right, top)`.
  self.graph = ox.graph_from_bbox(north, south, east, west, network_type="drive")


starting seed 1
game done generating, running
Iteration 5 gap:  0.14535099681064273
Iteration 10 gap:  0.1264210653119227
Iteration 15 gap:  0.10383443165675837
Iteration 20 gap:  0.08683392517605831
Iteration 25 gap:  0.07028046933275856
Iteration 30 gap:  0.059285554588806466
Iteration 35 gap:  0.05270438960294693
Iteration 40 gap:  0.04999572730042773
Iteration 45 gap:  0.04641321833343648
Iteration 50 gap:  0.044657369041795625
Iteration 55 gap:  0.042142880379374525
Iteration 60 gap:  0.04032990938218939
Iteration 65 gap:  0.03763216453758689
Iteration 70 gap:  0.03536933119948277
Iteration 75 gap:  0.03295244010591947
Iteration 80 gap:  0.031425840076561184
Iteration 85 gap:  0.029946049958607224
Iteration 90 gap:  0.02868678374566408
Iteration 95 gap:  0.027314165708890337
Iteration 100 gap:  0.025973965175459357
Iteration 105 gap:  0.02466928803224744
Iteration 110 gap:  0.023079975773515282
Iteration 115 gap:  0.02161439313105662
Iteration 120 gap:  0.02188274975497778
Iterati

In [23]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [1 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [False for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              1   
1        1              8              1              1   
2        1              8              1              1   
3        1              8              1              1   
4        1              8              1              1   
...    ...            ...            ...            ...   
1584    10              8              1              1   
1585    10              8              1              1   
1586    10              8              1              1   
1587    10              8              1              1   
1588    10              8              1              1   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1         False                1        0.637597   
1                          1         False                2        0.615524   
2                          1         False                3        0.623567   
3                          1         False                4        0.611487   
4                          1         False                5        0.637669   
...                      ...           ...              ...             ...   
1584                       1         False              155        0.617329   
1585                       1         False              156        0.618927   
1586                       1         False              157         0.61962   
1587                       1         False              158        0.618935   
1588                       1         False              159        0.634455   

          gaps  iteration_number  
0     0.145351                 5  
1     0.126421                10  
2     0.103834                15  
3     0.086834                20  
4      0.07028                25  
...        ...               ...  
1584  0.003111               775  
1585  0.003039               780  
1586  0.002986               785  
1587  0.002916               790  
1588  0.002864               795  

[1589 rows x 10 columns]

In [24]:
exploded_df.to_csv("ISG_NFG_PRMP_RANDOM_MATRIX.csv")

### ISG SF DO Random target values - use 3 defenders

In [6]:
import warnings
warnings.filterwarnings('ignore', category=FutureWarning)

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 3,
    "defender_penalty_factor": 3,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

# Bounding box for Hoboken, NJ
# bbox_hoboken_small = (40.752635, 40.745600, -74.030386,-74.043903)
bbox_hoboken_low = (40.745411, 40.735486, -74.025857,-74.041479)
bbox_hoboken_east = (40.748337, 40.734641,-74.022961,-74.031286)
bbox_downtown = (40.718721, 40.714078, -73.996074, -74.002651)
bbox_downtown_large = (40.7215, 40.710, -73.9935, -74.010)
# 40.7060, -74.0140, 40.7205, -73.9935
college_police = (40.743293077312465, -74.02670221027175)
police_station = (40.73768931976651, -74.02990519431108)
traffic_police = (40.7366602084371, -74.03449866349136)
downtown_station = (40.71232433042349, -74.00187755238431)
fifth_ave_station = (40.71637413934789, -73.9973285259067)
fifth_precinct = (40.71625547686622, -73.99736909131171)
booking_station = (40.716191530904815, -74.00102237385177)
police_plaza = (40.71236124409745, -74.00173715463521)
troop_nyc = (40.71657885026091, -74.00641139014367)
first_precinct = (40.720411300417446, -74.0070247584372)

num_timesteps_li = []
num_attackers_li = []
num_defenders_li = []
supports=[]
dims_li = []
dts = []
frs = []
defender_actions_sizes = []
attacker_actions_sizes = []
iterations_to_converge = []
iteration_times_li = []
gaps_li = []

isg = InfraSecurityGame(df_combined, ny_blocks_gdf, INFRA_WEIGHTS, bbox=bbox_downtown_large)
isg.generate(num_attackers=1,
             num_defenders=2,
             home_base_assignments=[(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza),(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza)],
             num_timesteps=8,
             generate_utility_matrix=False,
             random_target_values=False,
             force_return=True,
             defense_time_threshold=1,
             **general_sum_kwargs,
             **schedule_form_kwargs)

for seed in seeds:
    print(f"starting seed {seed}")
    
    sdict_copy = copy.deepcopy(isg.schedule_form_dict)
    sdict_copy["target_utilities"] = generate_random_target_utility_matrix_like(isg.schedule_form_dict["target_utilities"], general_sum=False, respect_sign_roles=True)
    
    D_a, D_d, u, A_a, A_d, c, iteration_times, gaps = double_oracle_sf(sdict_copy,eps=1e-12, verbose=False)
    support = sum([1 for p in D_d if p!=0])
    supports.append(support)
    iterations_to_converge.append(c)
    defender_actions_sizes.append(len(A_d))
    attacker_actions_sizes.append(len(A_a))
    iteration_times_li.append(iteration_times)
    gaps_li.append(gaps)

starting seed 1
Set parameter WLSAccessID
Set parameter WLSSecret
Set parameter LicenseID to value 2455389
Academic license 2455389 - for non-commercial use only - registered to jc___@columbia.edu
starting seed 2
starting seed 3
starting seed 4
starting seed 5
starting seed 6
starting seed 7
starting seed 8
starting seed 9
starting seed 10


In [7]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "def_support": supports,
    "iterations_to_converge": iterations_to_converge,
    "iteration_time": iteration_times_li,
    "gap": gaps_li,
    "defender_actions_size": defender_actions_sizes,
    "attacker_actions_size": attacker_actions_sizes
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_time", "gap"], ignore_index=True)

# Optional: Add a column for iteration number within each grouped trial
exploded_df["iteration_number"] = exploded_df.groupby(
    ["seed"]
).cumcount()

# Reorder if desired
cols = ["seed",
    "num_timesteps", "num_defenders", "defense_time_threshold",
    "iteration_number", "iteration_time", "gap", 
    "iterations_to_converge", "def_support", "defender_actions_size", "attacker_actions_size"
]
exploded_df = exploded_df[cols]

# Make iteration number 1-indexed
exploded_df["iteration_number"] += 1

exploded_df

seed  num_timesteps  num_defenders  defense_time_threshold  \
0       1              8              2                       1   
1       1              8              2                       1   
2       1              8              2                       1   
3       1              8              2                       1   
4       1              8              2                       1   
..    ...            ...            ...                     ...   
177    10              8              2                       1   
178    10              8              2                       1   
179    10              8              2                       1   
180    10              8              2                       1   
181    10              8              2                       1   

     iteration_number iteration_time       gap  iterations_to_converge  \
0                   1       0.395894  0.837534                      17   
1                   2       0.006168  0.231854                      17   
2                   3        0.00351  0.224866                      17   
3                   4       0.007668  0.572073                      17   
4                   5       0.010945  0.314634                      17   
..                ...            ...       ...                     ...   
177                17       0.012501  0.009932                      21   
178                18       0.013993  0.009124                      21   
179                19          0.013  0.017959                      21   
180                20       0.013525  0.009207                      21   
181                21       0.013472       0.0                      21   

     def_support  defender_actions_size  attacker_actions_size  
0              6                     17                      9  
1              6                     17                      9  
2              6                     17                      9  
3              6                     17                      9  
4              6                     17                      9  
..           ...                    ...                    ...  
177            8                     21                     10  
178            8                     21                     10  
179            8                     21                     10  
180            8                     21                     10  
181            8                     21                     10  

[182 rows x 11 columns]

In [8]:
exploded_df.to_csv("ISG_SF_DO_2DEF_RANDOM_TARGET_VALUES.csv")

### RM

In [ ]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=2, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.schedule_form_dict["defender_utility_matrix"], runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=False, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21723831433169066
Iteration 10 gap:  0.14765174788643387
Iteration 15 gap:  0.1314924131369276
Iteration 20 gap:  0.1435998288772009
Iteration 25 gap:  0.12814458742604062
Iteration 30 gap:  0.1718830760932452
Iteration 35 gap:  0.16831852444284062
Iteration 40 gap:  0.16956568288001417
Iteration 45 gap:  0.13604157333659822
Iteration 50 gap:  0.09908805556236855
Iteration 55 gap:  0.07813052646761287
Iteration 60 gap:  0.08332852474281444
Iteration 65 gap:  0.07646435928419515
Iteration 70 gap:  0.05947192522284883
Iteration 75 gap:  0.05231808026048684
Iteration 80 gap:  0.047424855799586885
Iteration 85 gap:  0.05648477198658325
Iteration 90 gap:  0.058452964853945744
Iteration 95 gap:  0.06096410254131007
Iteration 100 gap:  0.07723093188378699
Iteration 105 gap:  0.09702496515689274
Iteration 110 gap:  0.11276424676903507
Iteration 115 gap:  0.12304712278316787
Iteration 120 gap:  0.11589526099401376
Iteration 125 g

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_SF_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### RM+

In [ ]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=2, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.schedule_form_dict["defender_utility_matrix"], runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=True, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21723831433169066
Iteration 10 gap:  0.14765174788643387
Iteration 15 gap:  0.1314924131369276
Iteration 20 gap:  0.1435998288772009
Iteration 25 gap:  0.12814458742604062
Iteration 30 gap:  0.1718830760932452
Iteration 35 gap:  0.16831852444284062
Iteration 40 gap:  0.16956568288001417
Iteration 45 gap:  0.13604157333659822
Iteration 50 gap:  0.09908805556236855
Iteration 55 gap:  0.07813052646761287
Iteration 60 gap:  0.08332852474281444
Iteration 65 gap:  0.07646435928419515
Iteration 70 gap:  0.05947192522284883
Iteration 75 gap:  0.05231808026048684
Iteration 80 gap:  0.047424855799586885
Iteration 85 gap:  0.05648477198658325
Iteration 90 gap:  0.058452964853945744
Iteration 95 gap:  0.06096410254131007
Iteration 100 gap:  0.07723093188378699
Iteration 105 gap:  0.09702496515689274
Iteration 110 gap:  0.11276424676903507
Iteration 115 gap:  0.12304712278316787
Iteration 120 gap:  0.11589526099401376
Iteration 125 g

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_SF_RMP_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### PRM+

In [ ]:
df = pd.read_csv("lobeke.csv")
df.dropna(inplace=True)

# Lobeke National Park Bounding Box
# lat_min, lon_min = 2.05522, 15.8790
# lat_max, lon_max = 2.2837, 16.2038

lat_min, lon_min = 2.0530, 15.8790
lat_max, lon_max = 2.2837, 16.2038

coordinate_rectangle = [lat_min, lat_max, lon_min, lon_max]


boulou_camp = (2.2,15.9)
# lobeke_camp = (2.25,15.75)
kabo_djembe = (2.0532352380408088, 16.085709866529694)
bomassa = (2.2037280296158355, 16.187056364164913)
inner_post = (2.2,15.98)
sangha_river = [(2.2837, 16.16283352464626),(2.053, 16.066212728001727)]

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 5,
    "defender_penalty_factor": 5,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

gaps_li = []
interval_times_li = []
for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    gsg = GreenSecurityGame(df, coordinate_rectangle, "centroid", num_clusters=10, num_rows=7, num_columns=7)
    gsg.generate(num_attackers=1, 
                 num_defenders=2, 
                 home_base_assignments=[(kabo_djembe, bomassa, inner_post)], 
                 num_timesteps=8, 
                 generate_utility_matrix=True, 
                 random_target_values=True,
                 defense_time_threshold=1, 
                 generate_actions=False, 
                 force_return=True, 
                 general_sum=False, 
                 **schedule_form_kwargs)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(gsg.schedule_form_dict["defender_utility_matrix"], runtime=120, interval=5, iterations=10000, averaging=2, alternations=True, plus=True, predictive=True, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.21723831433169066
Iteration 10 gap:  0.14765174788643387
Iteration 15 gap:  0.1314924131369276
Iteration 20 gap:  0.1435998288772009
Iteration 25 gap:  0.12814458742604062
Iteration 30 gap:  0.1718830760932452
Iteration 35 gap:  0.16831852444284062
Iteration 40 gap:  0.16956568288001417
Iteration 45 gap:  0.13604157333659822
Iteration 50 gap:  0.09908805556236855
Iteration 55 gap:  0.07813052646761287
Iteration 60 gap:  0.08332852474281444
Iteration 65 gap:  0.07646435928419515
Iteration 70 gap:  0.05947192522284883
Iteration 75 gap:  0.05231808026048684
Iteration 80 gap:  0.047424855799586885
Iteration 85 gap:  0.05648477198658325
Iteration 90 gap:  0.058452964853945744
Iteration 95 gap:  0.06096410254131007
Iteration 100 gap:  0.07723093188378699
Iteration 105 gap:  0.09702496515689274
Iteration 110 gap:  0.11276424676903507
Iteration 115 gap:  0.12304712278316787
Iteration 120 gap:  0.11589526099401376
Iteration 125 g

In [36]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

num_timesteps  num_attackers  num_defenders  defense_time_threshold  \
0               8              1              1                       1   
1               8              1              1                       1   
2               8              1              1                       1   
3               8              1              1                       1   
4               8              1              1                       1   
5               8              1              1                       1   
6               8              1              1                       1   
7               8              1              1                       1   
8               8              1              1                       1   
9               8              1              1                       1   
10              8              1              1                       1   
11              8              1              1                       1   
12              8              1              1                       1   
13              8              1              1                       1   
14              8              1              1                       1   
15              8              1              1                       1   
16              8              1              1                       1   

    force_return  iteration_number iteration_times      gaps  
0           True                 0        0.192131  0.217238  
1           True                 1         0.21313  0.147652  
2           True                 2        0.171854  0.131492  
3           True                 3        0.180722    0.1436  
4           True                 4        0.178561  0.128145  
5           True                 5        0.188964  0.171883  
6           True                 6        0.238595  0.168319  
7           True                 7        0.222445  0.169566  
8           True                 0        0.211734   0.32868  
9           True                 1        0.170227  0.191657  
10          True                 2        0.184536  0.170677  
11          True                 3        0.179197  0.198217  
12          True                 4         0.19158  0.175843  
13          True                 5        0.196858   0.13175  
14          True                 6        0.183783  0.156964  
15          True                 7        0.170713  0.105948  
16          True                 8        0.212765  0.162613

In [ ]:
exploded_df.to_csv("GSG_SF_PRMP_RANDOM_TARGET_VALUES_TO_MATRIX.csv")

### RM random matrix

In [15]:
# Bounding box for Hoboken, NJ
# bbox_hoboken_small = (40.752635, 40.745600, -74.030386,-74.043903)
bbox_hoboken_low = (40.745411, 40.735486, -74.025857,-74.041479)
bbox_hoboken_east = (40.748337, 40.734641,-74.022961,-74.031286)
bbox_downtown = (40.718721, 40.714078, -73.996074, -74.002651)
bbox_downtown_large = (40.7215, 40.710, -73.9935, -74.010)
# 40.7060, -74.0140, 40.7205, -73.9935
college_police = (40.743293077312465, -74.02670221027175)
police_station = (40.73768931976651, -74.02990519431108)
traffic_police = (40.7366602084371, -74.03449866349136)
downtown_station = (40.71232433042349, -74.00187755238431)
fifth_ave_station = (40.71637413934789, -73.9973285259067)
fifth_precinct = (40.71625547686622, -73.99736909131171)
booking_station = (40.716191530904815, -74.00102237385177)
police_plaza = (40.71236124409745, -74.00173715463521)
troop_nyc = (40.71657885026091, -74.00641139014367)
first_precinct = (40.720411300417446, -74.0070247584372)

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 3,
    "defender_penalty_factor": 3,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

isg = InfraSecurityGame(df_combined, ny_blocks_gdf, INFRA_WEIGHTS, bbox=bbox_downtown_large)
isg.generate(num_attackers=1,
             num_defenders=2,
             home_base_assignments=[(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza),(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza)],
             num_timesteps=8,
             generate_utility_matrix=True,
             generate_actions=False,
             force_return=True,
             defense_time_threshold=1,
             **general_sum_kwargs,
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []

for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(isg.schedule_form_dict["defender_utility_matrix"]), high=np.max(isg.schedule_form_dict["defender_utility_matrix"]), size=isg.schedule_form_dict["defender_utility_matrix"].shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=0, alternations=False, plus=False, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.178158447080485
Iteration 10 gap:  0.14300964282900708
Iteration 15 gap:  0.12942154333371936
Iteration 20 gap:  0.10413627441476792
Iteration 25 gap:  0.1135771216794963
Iteration 30 gap:  0.08567828452640752
Iteration 35 gap:  0.07252459028846392
Iteration 40 gap:  0.07386617604729101
Iteration 45 gap:  0.07737935218773734
Iteration 50 gap:  0.07201417082553613
Iteration 55 gap:  0.06848666331057712
Iteration 60 gap:  0.06179413462703276
Iteration 65 gap:  0.06671239193552564
Iteration 70 gap:  0.06199461795535027
Iteration 75 gap:  0.05018340842145813
Iteration 80 gap:  0.0430892407364592
Iteration 85 gap:  0.0472128473731066
Iteration 90 gap:  0.047778382730492064
Iteration 95 gap:  0.048312640051640876
Iteration 100 gap:  0.04736621691359705
Iteration 105 gap:  0.04733105596878412
Iteration 110 gap:  0.047126408225920124
Iteration 115 gap:  0.04550016327445694
Iteration 120 gap:  0.041630919464665295
Iteration 125 g

In [16]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              2   
1        1              8              1              2   
2        1              8              1              2   
3        1              8              1              2   
4        1              8              1              2   
...    ...            ...            ...            ...   
2970    10              8              1              2   
2971    10              8              1              2   
2972    10              8              1              2   
2973    10              8              1              2   
2974    10              8              1              2   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1          True                1        0.397648   
1                          1          True                2        0.303803   
2                          1          True                3        0.327543   
3                          1          True                4        0.300531   
4                          1          True                5        0.303055   
...                      ...           ...              ...             ...   
2970                       1          True              298        0.358998   
2971                       1          True              299        0.288921   
2972                       1          True              300        0.317329   
2973                       1          True              301        0.330501   
2974                       1          True              302        0.293603   

          gaps  iteration_number  
0     0.178158                 5  
1      0.14301                10  
2     0.129422                15  
3     0.104136                20  
4     0.113577                25  
...        ...               ...  
2970  0.008254              1490  
2971   0.00891              1495  
2972  0.009434              1500  
2973    0.0098              1505  
2974  0.009969              1510  

[2975 rows x 10 columns]

In [17]:
exploded_df.to_csv("ISG_SF_RM_RANDOM_MATRIX.csv")

### RM+ random matrix

In [18]:
# Bounding box for Hoboken, NJ
# bbox_hoboken_small = (40.752635, 40.745600, -74.030386,-74.043903)
bbox_hoboken_low = (40.745411, 40.735486, -74.025857,-74.041479)
bbox_hoboken_east = (40.748337, 40.734641,-74.022961,-74.031286)
bbox_downtown = (40.718721, 40.714078, -73.996074, -74.002651)
bbox_downtown_large = (40.7215, 40.710, -73.9935, -74.010)
# 40.7060, -74.0140, 40.7205, -73.9935
college_police = (40.743293077312465, -74.02670221027175)
police_station = (40.73768931976651, -74.02990519431108)
traffic_police = (40.7366602084371, -74.03449866349136)
downtown_station = (40.71232433042349, -74.00187755238431)
fifth_ave_station = (40.71637413934789, -73.9973285259067)
fifth_precinct = (40.71625547686622, -73.99736909131171)
booking_station = (40.716191530904815, -74.00102237385177)
police_plaza = (40.71236124409745, -74.00173715463521)
troop_nyc = (40.71657885026091, -74.00641139014367)
first_precinct = (40.720411300417446, -74.0070247584372)

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 3,
    "defender_penalty_factor": 3,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

isg = InfraSecurityGame(df_combined, ny_blocks_gdf, INFRA_WEIGHTS, bbox=bbox_downtown_large)
isg.generate(num_attackers=1,
             num_defenders=2,
             home_base_assignments=[(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza),(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza)],
             num_timesteps=8,
             generate_utility_matrix=True,
             generate_actions=False,
             force_return=True,
             defense_time_threshold=1,
             **general_sum_kwargs,
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []

for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(isg.schedule_form_dict["defender_utility_matrix"]), high=np.max(isg.schedule_form_dict["defender_utility_matrix"]), size=isg.schedule_form_dict["defender_utility_matrix"].shape)
    print(random_matrix.shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=1, alternations=True, plus=True, predictive=False, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
(7396, 23)
game done generating, running
Iteration 5 gap:  0.1434879050173295
Iteration 10 gap:  0.13316205886750104
Iteration 15 gap:  0.11828153310746653
Iteration 20 gap:  0.10512808362094145
Iteration 25 gap:  0.09201359322505132
Iteration 30 gap:  0.0865495361388594
Iteration 35 gap:  0.07563164623547708
Iteration 40 gap:  0.0670333324768923
Iteration 45 gap:  0.06156892197326724
Iteration 50 gap:  0.0556195987050645
Iteration 55 gap:  0.049057965832766004
Iteration 60 gap:  0.04871185045933091
Iteration 65 gap:  0.04763569648897681
Iteration 70 gap:  0.04948396672358529
Iteration 75 gap:  0.04834571146789007
Iteration 80 gap:  0.0459052433001606
Iteration 85 gap:  0.04270703242600621
Iteration 90 gap:  0.039911413259860806
Iteration 95 gap:  0.037706284583196026
Iteration 100 gap:  0.03607066909315054
Iteration 105 gap:  0.034743939431198745
Iteration 110 gap:  0.034134924093812025
Iteration 115 gap:  0.03273258703295079
Iteration 120 gap:  0.031623632084182896
It

In [19]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              2   
1        1              8              1              2   
2        1              8              1              2   
3        1              8              1              2   
4        1              8              1              2   
...    ...            ...            ...            ...   
3043    10              8              1              2   
3044    10              8              1              2   
3045    10              8              1              2   
3046    10              8              1              2   
3047    10              8              1              2   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1          True                1        0.344302   
1                          1          True                2        0.294858   
2                          1          True                3        0.338747   
3                          1          True                4        0.288135   
4                          1          True                5        0.304355   
...                      ...           ...              ...             ...   
3043                       1          True              307        0.289813   
3044                       1          True              308        0.289063   
3045                       1          True              309        0.308479   
3046                       1          True              310        0.293677   
3047                       1          True              311        0.304796   

          gaps  iteration_number  
0     0.143488                 5  
1     0.133162                10  
2     0.118282                15  
3     0.105128                20  
4     0.092014                25  
...        ...               ...  
3043  0.000468              1535  
3044  0.000484              1540  
3045  0.000494              1545  
3046  0.000508              1550  
3047  0.000513              1555  

[3048 rows x 10 columns]

In [20]:
exploded_df.to_csv("ISG_SF_NEW_RMP_RANDOM_MATRIX.csv")

### PRM+ random matrix

In [21]:
# Bounding box for Hoboken, NJ
# bbox_hoboken_small = (40.752635, 40.745600, -74.030386,-74.043903)
bbox_hoboken_low = (40.745411, 40.735486, -74.025857,-74.041479)
bbox_hoboken_east = (40.748337, 40.734641,-74.022961,-74.031286)
bbox_downtown = (40.718721, 40.714078, -73.996074, -74.002651)
bbox_downtown_large = (40.7215, 40.710, -73.9935, -74.010)
# 40.7060, -74.0140, 40.7205, -73.9935
college_police = (40.743293077312465, -74.02670221027175)
police_station = (40.73768931976651, -74.02990519431108)
traffic_police = (40.7366602084371, -74.03449866349136)
downtown_station = (40.71232433042349, -74.00187755238431)
fifth_ave_station = (40.71637413934789, -73.9973285259067)
fifth_precinct = (40.71625547686622, -73.99736909131171)
booking_station = (40.716191530904815, -74.00102237385177)
police_plaza = (40.71236124409745, -74.00173715463521)
troop_nyc = (40.71657885026091, -74.00641139014367)
first_precinct = (40.720411300417446, -74.0070247584372)

schedule_form_kwargs = {
    "schedule_form": True,
    "simple": False,
    "attacker_penalty_factor": 3,
    "defender_penalty_factor": 3,
}

general_sum_kwargs = {
    "general_sum": False,
    "attacker_feature_value":  42, 
    "defender_feature_value": 69, 
    "defender_step_cost": 32.5, 
}

isg = InfraSecurityGame(df_combined, ny_blocks_gdf, INFRA_WEIGHTS, bbox=bbox_downtown_large)
isg.generate(num_attackers=1,
             num_defenders=2,
             home_base_assignments=[(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza),(fifth_precinct,booking_station, troop_nyc, first_precinct, police_plaza)],
             num_timesteps=8,
             generate_utility_matrix=True,
             generate_actions=False,
             force_return=True,
             defense_time_threshold=1,
             **general_sum_kwargs,
             **schedule_form_kwargs)

gaps_li = []
interval_times_li = []

for seed in seeds:
    print(f"starting seed {seed}")
    np.random.seed(seed)
    random_matrix = np.random.uniform(low=np.min(isg.schedule_form_dict["defender_utility_matrix"]), high=np.max(isg.schedule_form_dict["defender_utility_matrix"]), size=isg.schedule_form_dict["defender_utility_matrix"].shape)
    print("game done generating, running")
    D_d, U, gaps, interval_times = regret_matching(random_matrix, runtime=120, interval=5, iterations=10000, averaging=2, alternations=True, plus=True, predictive=True, verbose=True)
    gaps_li.append(gaps)
    interval_times_li.append(interval_times)

starting seed 1
game done generating, running
Iteration 5 gap:  0.14366244517940585
Iteration 10 gap:  0.12229160224701591
Iteration 15 gap:  0.10156036489591885
Iteration 20 gap:  0.08602016961791908
Iteration 25 gap:  0.07616078599147807
Iteration 30 gap:  0.07532834613876321
Iteration 35 gap:  0.06770209373388264
Iteration 40 gap:  0.05989880064736708
Iteration 45 gap:  0.05132756393916521
Iteration 50 gap:  0.04181188003991587
Iteration 55 gap:  0.04071194392325467
Iteration 60 gap:  0.04183636078041886
Iteration 65 gap:  0.040548996586564856
Iteration 70 gap:  0.040047974048508406
Iteration 75 gap:  0.03860708569339111
Iteration 80 gap:  0.036791009288510756
Iteration 85 gap:  0.034948662511549655
Iteration 90 gap:  0.03237671160986094
Iteration 95 gap:  0.03024198325150451
Iteration 100 gap:  0.02788550278719798
Iteration 105 gap:  0.025989785438400803
Iteration 110 gap:  0.024689930153464323
Iteration 115 gap:  0.02355396323728337
Iteration 120 gap:  0.022926137841706107
Iterati

In [22]:
df = pd.DataFrame({
    "seed":seeds,
    "num_timesteps": [8 for i in range(len(seeds))],
    "num_attackers": [1 for i in range(len(seeds))],
    "num_defenders": [2 for i in range(len(seeds))],
    "defense_time_threshold": [1 for i in range(len(seeds))],
    "force_return": [True for i in range(len(seeds))],
    "iteration_times": interval_times_li,
    "gaps": gaps_li
})

# Step 2: Explode list columns
exploded_df = df.explode(["iteration_times", "gaps"], ignore_index=True)

# Optional: Add a column for iteration number within each trial
exploded_df["interval_number"] = exploded_df.groupby(["seed"]).cumcount()

# Reorder if desired
cols = ["seed","num_timesteps", "num_attackers", "num_defenders", "defense_time_threshold", "force_return", "interval_number", "iteration_times", "gaps"]
exploded_df = exploded_df[cols]

exploded_df["interval_number"] = exploded_df["interval_number"]+1
exploded_df["iteration_number"] = exploded_df["interval_number"]*5
exploded_df

seed  num_timesteps  num_attackers  num_defenders  \
0        1              8              1              2   
1        1              8              1              2   
2        1              8              1              2   
3        1              8              1              2   
4        1              8              1              2   
...    ...            ...            ...            ...   
3117    10              8              1              2   
3118    10              8              1              2   
3119    10              8              1              2   
3120    10              8              1              2   
3121    10              8              1              2   

      defense_time_threshold  force_return  interval_number iteration_times  \
0                          1          True                1        0.338686   
1                          1          True                2        0.321789   
2                          1          True                3        0.298274   
3                          1          True                4        0.286134   
4                          1          True                5        0.268882   
...                      ...           ...              ...             ...   
3117                       1          True              314        0.328199   
3118                       1          True              315          0.3336   
3119                       1          True              316        0.268796   
3120                       1          True              317        0.322298   
3121                       1          True              318        0.337358   

          gaps  iteration_number  
0     0.143662                 5  
1     0.122292                10  
2      0.10156                15  
3      0.08602                20  
4     0.076161                25  
...        ...               ...  
3117  0.000217              1570  
3118  0.000215              1575  
3119  0.000211              1580  
3120  0.000209              1585  
3121  0.000205              1590  

[3122 rows x 10 columns]

In [23]:
exploded_df.to_csv("ISG_SF_PRMP_RANDOM_MATRIX.csv")